In [2]:
import pandas as pd
import nltk
import numpy as np
import pickle as pkl

from gensim.models.fasttext import load_facebook_vectors
from nltk.tokenize import word_tokenize

from sklearn.model_selection import GridSearchCV

from sklearn.svm import SVC 

In [3]:
songs = pd.read_csv("../resource/asnlib/publicdata/SingleLabel.csv")
songs

artist    genre                  title                    album  \
0            Nirvana     Rock  You Know You’re Right                  Nirvana   
1      Damian Marley   Reggae             Here We Go               Stony Hill   
2     The Mission UK     Rock                   Jade  Another Fall from Grace   
3               UB40   Reggae       Food For Thought              Signing Off   
4        Johnny Cash  Country   I’ve Been Everywhere   American II: Unchained   
...              ...      ...                    ...                      ...   
1155     The Beatles     Rock              Yesterday                    Help!   
1156     The Sundays     Rock                   Love                    Blind   
1157        The Cure     Rock        Killing an Arab           Boys Don’t Cry   
1158    Garth Brooks  Country                    Mom      Man Against Machine   
1159    Alan Jackson  Country        The Older I Get                      NaN   

        year                                             lyrics       label  
0     2002.0  I will never bother you\nI will never promise ...     Sadness  
1     2017.0  Here we go\nMy big ego is gonna get me in trou...     Tension  
2     2016.0  She came as Lolita dressed as Venus\nAnd adorn...  Tenderness  
3     1980.0  Ivory Madonna, dying in the dust\nWaiting for ...     Sadness  
4     1996.0  I was totin' my pack along the dusty Winnemucc...     Sadness  
...      ...                                                ...         ...  
1155  1965.0  Yesterday\nAll my troubles seemed so far away\...     Sadness  
1156  1992.0  Picture myself as a thin white child\nBack to ...  Tenderness  
1157  1978.0  Standing on the beach\nWith a gun in my hand\n...     Tension  
1158  2014.0  A little baby told God\nHey I'm kinda scared, ...  Tenderness  
1159  2017.0  The older I get\nThe more I think\nYou only ge...     Sadness  

[1160 rows x 7 columns]

In [4]:
with open("../resource/asnlib/publicdata/subset.pkl", "rb") as f:
    embeddings = pkl.load(f)
embeddings

{'bloodline': array([-0.01797874,  0.02653708,  0.01696954,  0.05666937, -0.02392901,
        -0.08199249, -0.00860746, -0.06023632, -0.02977115,  0.04680225,
         0.02055368,  0.0100565 , -0.12607269, -0.08220278, -0.02330518,
         0.03285089,  0.0591183 , -0.0468577 , -0.04384419, -0.02700686,
         0.0503712 , -0.05494036, -0.07479937, -0.09335661,  0.02826717,
         0.00559966,  0.04848999,  0.03684146, -0.03696519,  0.07282916,
         0.01597533, -0.01071503,  0.05531365, -0.01210256, -0.0697739 ,
         0.01461262, -0.00874667,  0.00239845,  0.0080654 ,  0.00355965,
         0.04255512, -0.00658994,  0.01902088, -0.01206092, -0.05457998,
        -0.01288679,  0.00996237, -0.01132237, -0.09321052,  0.00037116,
        -0.0301162 , -0.04740999,  0.07016359,  0.04068878, -0.0102009 ,
         0.03219822, -0.00018068,  0.0125285 , -0.02238367,  0.13929306,
        -0.01047499,  0.02163016, -0.01486643,  0.00610404, -0.02075699,
         0.02676238, -0.0115975 ,  0.0

In [13]:
# PART 1. Preprocess the data and create a variable `song_words`
# that contains a list with one entry for each row in the `songs` dataframe.
# Each entry should be a list of the tokenized words for that song's lyrics,
# as specified in the lab document.

###
### YOUR CODE HERE
###

from nltk.corpus import stopwords

# tokenizing words
song_words_unfiltered = []
song_words = []

lyrics = songs["lyrics"].to_numpy()

for song in lyrics:
    tokenized = word_tokenize(song)
    
    # convert to lowercase
    lowered = []
    for word in tokenized:
        lowered.append(word.lower())
    song_words_unfiltered.append(lowered)

# removing stopwords
stop_words = set(stopwords.words('english'))

for song in song_words_unfiltered:
    song_filtered = []
    for word in song:
        if word not in stop_words:
            song_filtered.append(word)
    song_words.append(song_filtered)

In [6]:
###
### AUTOGRADER TEST - DO NOT REMOVE
###


In [15]:
# PART 2. Create the song embeddings and store them as a matrix in a variable `X`
# where the rows are the songs and the columns are the vector dimensions.

###
### YOUR CODE HERE
###

# each song
def avg(song, embeddings):
    word_vecs = []
    # each word in song
    for word in song:
        # add word vector or zero vector
        if word in embeddings.keys():
            word_vecs.append(embeddings[word])
        else:
            word_vecs.append(np.zeros(300))
    # average word vectors, collect averages
    return np.mean(word_vecs, axis=0)

X = np.array([avg(song, embeddings) for song in song_words])

array([[-0.00957003,  0.00431863,  0.04379523, ...,  0.06417704,
        -0.02450218, -0.0340887 ],
       [-0.00953266, -0.04976596, -0.03056127, ...,  0.13356681,
        -0.0391228 , -0.05483808],
       [-0.00822194, -0.00720247, -0.00065503, ...,  0.10405368,
         0.00571181, -0.00614691],
       ...,
       [ 0.0195359 , -0.00152443,  0.02811773, ...,  0.09016223,
         0.00103493, -0.03683022],
       [ 0.02309448, -0.07944541, -0.01446055, ...,  0.0866708 ,
         0.01459899,  0.00016242],
       [ 0.00989324, -0.03892756, -0.01309008, ...,  0.05997116,
         0.01380511,  0.01327634]])

In [ ]:
###
### AUTOGRADER TEST - DO NOT REMOVE
###


In [20]:
# PART 3. Train the predictors as described in the lab document.
# Create a variable `accuracy` storing the accuracy of the best model,
# as well as a variable `n_vecs` storing the number of support vectors.

###
### YOUR CODE HERE
###

from sklearn.metrics import accuracy_score

# target mood labels
y = songs["label"]

# create SVMs
parameters = {
    'C': [.00001, .0001, .001, .01, .1, 1],
    'gamma': [0.00001, 0.00005, 0.0001, 0.0005, 0.001, 0.005],
    'kernel': ['poly', 'rbf']
}

svm = SVC()
clf = GridSearchCV(svm, parameters, cv=5, scoring='accuracy', verbose=1)

# finding accuracy and number of support vectors of best model <3
clf.fit(X, y)
y_pred = clf.predict(X)
accuracy = accuracy_score(y, y_pred)
n_vecs = clf.best_estimator_.n_support_.sum()

print("Accuracy:", accuracy)
print("Number of support vectors:", n_vecs)

Fitting 5 folds for each of 72 candidates, totalling 360 fits
Accuracy: 0.49051724137931035
Number of support vectors: 917


In [ ]:
###
### AUTOGRADER TEST - DO NOT REMOVE
###


In [ ]:
# PART 4. Answer the discussion questions in comments here.

# No, it is not a good model.

# 1. The accuracy score is 0.49. This means that the model has less than a 50% chance
#    of correctly labeling the song's emotion. That sucks! Random guessing would yield an
#    accuracy score of around 0.11; the model's accuracy score isn't super close to that,
#    but it is definitely not far enough.

# 2. The number of support vectors is 917. The number of songs the model was trained on is
#    1160. This means that the vast majority of the songs were determining factors for
#    classification, which also sucks. It means that the model is way too complex; it is
#    trying to map closely to the training data, meaning that it would generalize really
#    poorly. And even now, the accuracy is still really bad.